# Multi INput Multi-Step Output

In [9]:
import pandas as pd
from matplotlib import pyplot as plt
from sklearn.linear_model import LinearRegression
from keras.layers import Bidirectional
import os
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense
from tensorflow.keras.layers import LSTM
import datetime
from numpy import hstack, vstack
from numpy import array
from sklearn.linear_model import SGDClassifier as SGD

In [3]:
# list team names

teams = ['Minnesota Timberwolves',
 'Utah Jazz',
 'Philadelphia 76ers',
 'San Antonio Spurs',
 'Brooklyn Nets',
 'Detroit Pistons',
 'Washington Wizards',
 'Portland Trail Blazers',
 'Sacramento Kings',
 'Charlotte Hornets',
 'Miami Heat',
 'Boston Celtics',
 'Oklahoma City Thunder',
 'Dallas Mavericks',
 'New Orleans Pelicans',
 'Toronto Raptors',
 'New York Knicks',
 'LA Clippers',
 'Golden State Warriors',
 'Orlando Magic',
 'Indiana Pacers',
 'Cleveland Cavaliers',
 'Houston Rockets',
 'Memphis Grizzlies',
 'Phoenix Suns',
 'Milwaukee Bucks',
 'Denver Nuggets',
 'Chicago Bulls',
 'Los Angeles Lakers',
 'Atlanta Hawks']

In [21]:
for t in range(len(teams) - 1):


    #obtain list of dates
    directory = f"Historical/{teams[t]}"
    list_dates = []
    names = []
    for filename in os.listdir(directory):
        names.append(filename)
        if filename.endswith(".csv"):
            list_dates.append(filename)

    # create dictionary 
    final_data = {}

    # for minutes

    minutes = {}

    opponents = {}
    # reads in each csv
    for i in list_dates:
        data = pd.read_csv(f"{directory}/{i}", index_col=0)
        #gathers data and adds to dict
        date = data["Date"].tolist()[0]

        min_data = data.copy()



        minute = data["MIN"].tolist()

        minute_array = []

        for i in minute:
            time = i.split(":")

            minute_array.append(int(time[0]) + (int(time[0]) / 60))

        # (error for now) opponents[date] = data["Opponent"][0]

        data["MIN"] = minute_array

        data[date] = data["Score"]
        min_data[date] = data["MIN"]

        final_data[date] = data[date]
        minutes[date] = min_data[date]

    # convert dict to dataframe
    data_df = pd.DataFrame(final_data)
    
    # convert dict to dataframe
    min_df = pd.DataFrame(minutes)
    
    opp = pd.DataFrame.transpose(pd.DataFrame.from_dict(opponents, orient="index"))
    data_df = data_df.append(opp)

    tester = pd.DataFrame.transpose(data_df)

    tester["Datetime"] = pd.to_datetime(data_df.columns.tolist()).tolist()

    tester = tester.sort_values(by="Datetime")

    columns = tester.columns.tolist()[:-1]

    tester_min = pd.DataFrame.transpose(min_df)

    tester_min["Datetime"] = pd.to_datetime(min_df.columns.tolist()).tolist()

    tester_min = tester_min.sort_values(by="Datetime")

    columns = tester_min.columns.tolist()[:-1]
    
    add = {}



    #iterate through index
    for column in columns:
        print(column)

    # univariate data prep LSTM

        # split sequence
        def split_sequence(sequence, n_steps):
            X, y = list(), list()
            for i in range(len(sequence)):
                # find end of pattern 
                end_ix = i + n_steps
                #check if beyond sequence to break
                if end_ix > len(sequence):
                    break
                #gather input and output parts of the pattern
                seq_x, seq_y = sequence[i:end_ix, :-1], sequence[end_ix-1, -1]
                X.append(seq_x)
                y.append(seq_y)
            return array(X), array(y)
        # sequence
        df = tester[[column]]

        df["Min"] = tester_min[column].tolist()

        name = df.columns[0]

        rent_rate = array(df[name])

        # number of steps
        rent_rate = array(tester[column].dropna())
        predict = rent_rate
        eff = array(df["Min"].dropna())


        n_steps = 3
        if len(rent_rate) < 5:
            continue   


        # convert to [rows, columns] structure
        rent_rate = rent_rate.reshape((len(rent_rate), 1))
        eff = eff.reshape((len(eff), 1))
        predict = predict.reshape((len(predict), 1))


        # horizontally stack columns
        dataset = hstack((rent_rate, eff, predict))
        
        opt = 'adam'

        X, y = split_sequence(dataset, n_steps)

        X = X.astype(float)
        # summarize the data
        for i in range(len(X)):
            print(X[i], y[i])

        # reshape from [samples, timesteps] into [samples, timesteps, features]
        n_features = X.shape[2]
        
        if t == 0:
            
            print("True")
            model = Sequential()
            model.add(Bidirectional(LSTM(50, activation='relu', return_sequences=True, input_shape=(n_steps, n_features))))
            model.add(Bidirectional(LSTM(50, activation='relu', return_sequences=True, input_shape=(n_steps, n_features))))
            model.add(Bidirectional(LSTM(50, activation='relu', return_sequences=True, input_shape=(n_steps, n_features))))
            model.add(Dense(1))
            model.compile(optimizer=opt, loss='binary_crossentropy')
            
            X_old = X.copy()
            
            y_old = y.copy()
            
            # fit model
            model.fit(X, y, epochs=200, batch_size=32, verbose=0)
        
        else:
            
            # create a composite dataset of old and new data
            X_both, y_both = vstack((X_old, X)), hstack((y_old, y))
            # fit the model on new data
            model.fit(X_both, y_both, epochs=100, batch_size=32, verbose=0)
            
        




Bojan Bogdanovic
[[32.5        28.46666667]
 [22.25       33.55      ]
 [20.         28.46666667]] 20.0
[[22.25       33.55      ]
 [20.         28.46666667]
 [29.         25.41666667]] 29.0
[[20.         28.46666667]
 [29.         25.41666667]
 [30.75       32.53333333]] 30.75
[[29.         25.41666667]
 [30.75       32.53333333]
 [21.75       31.51666667]] 21.75
[[30.75       32.53333333]
 [21.75       31.51666667]
 [23.75       30.5       ]] 23.75
[[21.75       31.51666667]
 [23.75       30.5       ]
 [34.25       30.5       ]] 34.25
[[23.75 30.5 ]
 [34.25 30.5 ]
 [29.25 33.55]] 29.25
[[34.25       30.5       ]
 [29.25       33.55      ]
 [20.         31.51666667]] 20.0
[[29.25       33.55      ]
 [20.         31.51666667]
 [20.75       30.5       ]] 20.75
[[20.         31.51666667]
 [20.75       30.5       ]
 [10.         31.51666667]] 10.0
[[20.75       30.5       ]
 [10.         31.51666667]
 [39.5        28.46666667]] 39.5
[[10.         31.51666667]
 [39.5        28.46666667]
 [

/var/folders/g3/164q6cz52jv0sjllnsg7jdsm0000gn/T/ipykernel_5048/2343098578.py:57: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data_df = data_df.append(opp)
/var/folders/g3/164q6cz52jv0sjllnsg7jdsm0000gn/T/ipykernel_5048/2343098578.py:102: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["Min"] = tester_min[column].tolist()
2022-11-08 21:16:02.005918: I tensorflow/core/common_runtime/pluggable_device/pluggable_device_factory.cc:305] Could not identify NUMA node of platform GPU ID 0, defaulting to 0. Your kernel may not have been built with NUMA support.
2022-11-08 21:16:02.006182: I tensorflow/core/common_runtime/pluggable_device/pluggable_device_factory.cc:

Danuel House Jr.
[[27.         25.41666667]
 [ 1.25       12.2       ]
 [ 9.5        15.25      ]] 9.5
[[ 1.25       12.2       ]
 [ 9.5        15.25      ]
 [ 6.75       11.18333333]] 6.75
[[ 9.5        15.25      ]
 [ 6.75       11.18333333]
 [36.75       42.7       ]] 36.75
[[ 6.75       11.18333333]
 [36.75       42.7       ]
 [ 4.75       11.18333333]] 4.75
[[36.75       42.7       ]
 [ 4.75       11.18333333]
 [30.         15.25      ]] 30.0
[[ 4.75       11.18333333]
 [30.         15.25      ]
 [12.5        16.26666667]] 12.5
[[30.         15.25      ]
 [12.5        16.26666667]
 [ 4.5        15.25      ]] 4.5
[[12.5        16.26666667]
 [ 4.5        15.25      ]
 [ 8.5        15.25      ]] 8.5
[[ 4.5  15.25]
 [ 8.5  15.25]
 [18.75 21.35]] 18.75
[[ 8.5        15.25      ]
 [18.75       21.35      ]
 [15.25       16.26666667]] 15.25
[[18.75       21.35      ]
 [15.25       16.26666667]
 [17.25       16.26666667]] 17.25
[[15.25       16.26666667]
 [17.25       16.26666667]
 [ 8.75

/var/folders/g3/164q6cz52jv0sjllnsg7jdsm0000gn/T/ipykernel_5048/2343098578.py:102: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["Min"] = tester_min[column].tolist()
2022-11-08 21:17:03.651479: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:113] Plugin optimizer for device_type GPU is enabled.


Denzel Valentine
Donovan Mitchell
[[32.75       28.46666667]
 [43.75       37.61666667]
 [33.5        34.56666667]] 33.5
[[43.75       37.61666667]
 [33.5        34.56666667]
 [32.25       23.38333333]] 32.25
[[33.5        34.56666667]
 [32.25       23.38333333]
 [47.75       35.58333333]] 47.75
[[32.25       23.38333333]
 [47.75       35.58333333]
 [40.         32.53333333]] 40.0
[[47.75       35.58333333]
 [40.         32.53333333]
 [58.         32.53333333]] 58.0
[[40.         32.53333333]
 [58.         32.53333333]
 [52.5        36.6       ]] 52.5
[[58.         32.53333333]
 [52.5        36.6       ]
 [39.75       32.53333333]] 39.75
[[52.5        36.6       ]
 [39.75       32.53333333]
 [46.25       32.53333333]] 46.25
[[39.75       32.53333333]
 [46.25       32.53333333]
 [45.75       32.53333333]] 45.75
[[46.25       32.53333333]
 [45.75       32.53333333]
 [45.5        37.61666667]] 45.5
[[45.75       32.53333333]
 [45.5        37.61666667]
 [25.75       22.36666667]] 25.75
[[4

...

/var/folders/g3/164q6cz52jv0sjllnsg7jdsm0000gn/T/ipykernel_5048/2343098578.py:102: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["Min"] = tester_min[column].tolist()


Xavier Sneed
[[0.         2.03333333]
 [4.75       9.15      ]
 [1.25       2.03333333]] 1.25
[[4.75       9.15      ]
 [1.25       2.03333333]
 [2.         5.08333333]] 2.0
[[1.25       2.03333333]
 [2.         5.08333333]
 [0.         2.03333333]] 0.0
[[2.         5.08333333]
 [0.         2.03333333]
 [0.         5.08333333]] 0.0
[[0.         2.03333333]
 [0.         5.08333333]
 [4.         3.05      ]] 4.0


/var/folders/g3/164q6cz52jv0sjllnsg7jdsm0000gn/T/ipykernel_5048/2343098578.py:102: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["Min"] = tester_min[column].tolist()


Zylan Cheatham


/var/folders/g3/164q6cz52jv0sjllnsg7jdsm0000gn/T/ipykernel_5048/2343098578.py:102: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["Min"] = tester_min[column].tolist()


In [37]:
# number of steps
rent_rate = array(tester[column].dropna())
predict = rent_rate
eff = array(df["Min"].dropna())


In [43]:
rent_rate = rent_rate.tolist().pop(-1)

In [22]:


#obtain list of dates
directory = f"Historical/{teams[-1]}"
list_dates = []
names = []
for filename in os.listdir(directory):
    names.append(filename)
    if filename.endswith(".csv"):
        list_dates.append(filename)
        
# create dictionary 
test_data = {}

# for minutes

minutes_data = {}

opponents = {}
# reads in each csv
for i in list_dates:
    data = pd.read_csv(f"{directory}/{i}", index_col=0)
    #gathers data and adds to dict
    date = data["Date"].tolist()[0]
    
    min_data = data.copy()
    
    
    
    minute = data["MIN"].tolist()
    
    minute_array = []
    
    for i in minute:
        time = i.split(":")
        
        minute_array.append(int(time[0]) + (int(time[0]) / 60))
    
    # (error for now) opponents[date] = data["Opponent"][0]
    
    data["MIN"] = minute_array
    
    data[date] = data["Score"]
    min_data[date] = data["MIN"]
    
    test_data[date] = data[date]
    minutes_data[date] = min_data[date]
    
# convert dict to dataframe
test_df = pd.DataFrame(test_data)
test_df.head()

11/26/2021  01/23/2022  04/06/2022  11/27/2021  \
Bogdan Bogdanovic        22.75         NaN        29.5        6.75   
Cam Reddish              26.25         NaN         NaN        3.00   
Cameron Oliver             NaN         NaN         NaN         NaN   
Cat Barber                 NaN         NaN         NaN         NaN   
Chaundee Brown Jr.         NaN         NaN         NaN         NaN   

                    04/10/2022  03/31/2022  03/25/2022  03/30/2022  \
Bogdan Bogdanovic         38.0        16.5         NaN        32.0   
Cam Reddish                NaN         NaN         NaN         NaN   
Cameron Oliver             NaN         NaN         NaN         NaN   
Cat Barber                 NaN         NaN         NaN         NaN   
Chaundee Brown Jr.         NaN         NaN         NaN         NaN   

                    03/18/2022  04/05/2022  ...  03/28/2022  03/14/2022  \
Bogdan Bogdanovic         45.0       38.75  ...       37.25       26.25   
Cam Reddish                NaN         NaN  ...         NaN         NaN   
Cameron Oliver             NaN         NaN  ...         NaN         NaN   
Cat Barber                 NaN         NaN  ...         NaN         NaN   
Chaundee Brown Jr.         NaN         NaN  ...         NaN         NaN   

                    01/05/2022  11/14/2021  01/07/2022  03/16/2022  \
Bogdan Bogdanovic          NaN       14.50        26.0        21.0   
Cam Reddish               29.5       13.25         3.5         NaN   
Cameron Oliver             NaN         NaN         NaN         NaN   
Cat Barber                 NaN         NaN         NaN         NaN   
Chaundee Brown Jr.         NaN         NaN         NaN         NaN   

                    03/03/2022  01/12/2022  11/03/2021  11/17/2021  
Bogdan Bogdanovic         34.0       29.25       19.50       24.25  
Cam Reddish                NaN         NaN        5.75       31.00  
Cameron Oliver             NaN         NaN         NaN         NaN  
Cat Barber                 NaN         NaN         NaN         NaN  
Chaundee Brown Jr.         NaN         NaN         NaN         NaN  

[5 rows x 82 columns]

In [23]:
# convert dict to dataframe
min_test = pd.DataFrame(minutes_data)
min_test.tail()

11/26/2021  01/23/2022  04/06/2022  11/27/2021  \
Skylar Mays                     NaN    1.016667    1.016667         NaN   
Solomon Hill               5.083333         NaN         NaN       12.20   
Timothe Luwawu-Cabarrot    5.083333    1.016667         NaN       12.20   
Trae Young                27.450000   34.566667   37.616667       39.65   
Wes Iwundu                      NaN         NaN         NaN         NaN   

                         04/10/2022  03/31/2022  03/25/2022  03/30/2022  \
Skylar Mays                1.016667    5.083333         NaN         NaN   
Solomon Hill                    NaN         NaN         NaN         NaN   
Timothe Luwawu-Cabarrot    7.116667   27.450000   16.266667   23.383333   
Trae Young                34.566667   28.466667   39.650000   29.483333   
Wes Iwundu                      NaN         NaN         NaN         NaN   

                         03/18/2022  04/05/2022  ...  03/28/2022  03/14/2022  \
Skylar Mays                1.016667         NaN  ...         NaN         NaN   
Solomon Hill                    NaN         NaN  ...         NaN         NaN   
Timothe Luwawu-Cabarrot   20.333333   21.350000  ...        30.5    7.116667   
Trae Young                      NaN   37.616667  ...        36.6   38.633333   
Wes Iwundu                      NaN         NaN  ...         NaN         NaN   

                         01/05/2022  11/14/2021  01/07/2022  03/16/2022  \
Skylar Mays                     NaN    1.016667    2.033333         NaN   
Solomon Hill                    NaN    1.016667         NaN         NaN   
Timothe Luwawu-Cabarrot        36.6    2.033333   23.383333   10.166667   
Trae Young                      NaN   31.516667   35.583333   38.633333   
Wes Iwundu                      NaN         NaN         NaN         NaN   

                         03/03/2022  01/12/2022  11/03/2021  11/17/2021  
Skylar Mays                     NaN    2.033333         NaN         NaN  
Solomon Hill                    NaN         NaN         NaN         NaN  
Timothe Luwawu-Cabarrot         NaN   12.200000         NaN    0.000000  
Trae Young                37.616667   32.533333        36.6   35.583333  
Wes Iwundu                      NaN         NaN         NaN         NaN  

[5 rows x 82 columns]

In [24]:
tester

Bojan Bogdanovic  Danuel House Jr.  Denzel Valentine  \
10/20/2021             32.50               NaN               NaN   
10/22/2021             22.25               NaN               NaN   
10/26/2021             20.00               NaN               NaN   
10/28/2021             29.00               NaN               NaN   
10/30/2021             30.75               NaN               NaN   
...                      ...               ...               ...   
04/02/2022             27.75              7.50               NaN   
04/05/2022             27.50             18.75               NaN   
04/06/2022             32.75             21.00               NaN   
04/08/2022             36.25             20.25               NaN   
04/10/2022               NaN             16.50               NaN   

            Donovan Mitchell  Elijah Hughes  Eric Paschall  Greg Monroe  \
10/20/2021             32.75           2.00           8.75          NaN   
10/22/2021             43.75            NaN           6.75          NaN   
10/26/2021             33.50            NaN           7.50          NaN   
10/28/2021             32.25           1.25          23.50          NaN   
10/30/2021             47.75            NaN           4.00          NaN   
...                      ...            ...            ...          ...   
04/02/2022             39.75            NaN            NaN          NaN   
04/05/2022             40.75            NaN            NaN          NaN   
04/06/2022               NaN            NaN           4.25         7.75   
04/08/2022             36.25            NaN            NaN          NaN   
04/10/2022               NaN            NaN           8.25          NaN   

            Hassan Whiteside  Jared Butler  Joe Ingles  ...  \
10/20/2021             24.00          2.25       24.25  ...   
10/22/2021             22.75          0.00        0.00  ...   
10/26/2021             16.50          2.00       30.75  ...   
10/28/2021             18.50         17.00       24.75  ...   
10/30/2021             13.00          3.75       19.00  ...   
...                      ...           ...         ...  ...   
04/02/2022              6.50           NaN         NaN  ...   
04/05/2022             34.50           NaN         NaN  ...   
04/06/2022             40.25         36.00         NaN  ...   
04/08/2022             21.25          5.00         NaN  ...   
04/10/2022             23.75         17.75         NaN  ...   

            Nickeil Alexander-Walker  Norvel Pelle  Royce O'Neale  Rudy Gay  \
10/20/2021                       NaN           NaN          12.00       NaN   
10/22/2021                       NaN           NaN          25.00       NaN   
10/26/2021                       NaN           NaN          16.25       NaN   
10/28/2021                       NaN           NaN          19.50       NaN   
10/30/2021                       NaN           NaN          19.75       NaN   
...                              ...           ...            ...       ...   
04/02/2022                       NaN           NaN           8.50       NaN   
04/05/2022                       NaN           NaN          12.50      5.25   
04/06/2022                     18.75           NaN            NaN     31.50   
04/08/2022                       NaN           NaN           7.75       NaN   
04/10/2022                      6.50           NaN           9.25     17.00   

            Rudy Gobert  Trent Forrest  Udoka Azubuike  Xavier Sneed  \
10/20/2021        43.75            NaN             NaN           NaN   
10/22/2021        47.00           5.00             NaN           NaN   
10/26/2021        43.00            NaN             NaN           NaN   
10/28/2021        36.00           4.50             NaN           NaN   
10/30/2021        50.25           0.75             NaN           NaN   
...                 ...            ...             ...           ...   
04/02/2022        43.50            NaN             NaN           NaN   
04/05/2022  

In [25]:
opp = pd.DataFrame.transpose(pd.DataFrame.from_dict(opponents, orient="index"))
data_df = data_df.append(opp)

tester = pd.DataFrame.transpose(test_df)

tester["Datetime"] = pd.to_datetime(test_df.columns.tolist()).tolist()

tester = tester.sort_values(by="Datetime")

columns = tester.columns.tolist()[:-1]

tester_min = pd.DataFrame.transpose(min_test)

tester_min["Datetime"] = pd.to_datetime(min_test.columns.tolist()).tolist()

tester_min = tester_min.sort_values(by="Datetime")

columns = tester_min.columns.tolist()[:-1]

tester

/var/folders/g3/164q6cz52jv0sjllnsg7jdsm0000gn/T/ipykernel_5048/85995519.py:2: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data_df = data_df.append(opp)


Bogdan Bogdanovic  Cam Reddish  Cameron Oliver  Cat Barber  \
10/21/2021              22.25        27.25             NaN         NaN   
10/23/2021              11.00        28.00             NaN         NaN   
10/25/2021              20.25        30.00             NaN         NaN   
10/27/2021              23.25        10.75             NaN         NaN   
10/28/2021              30.00        26.25             NaN         NaN   
...                       ...          ...             ...         ...   
04/02/2022              15.75          NaN             NaN         NaN   
04/05/2022              38.75          NaN             NaN         NaN   
04/06/2022              29.50          NaN             NaN         NaN   
04/08/2022              42.25          NaN             NaN         NaN   
04/10/2022              38.00          NaN             NaN         NaN   

            Chaundee Brown Jr.  Clint Capela  Danilo Gallinari  \
10/21/2021                 NaN         31.75               NaN   
10/23/2021                 NaN         32.50               NaN   
10/25/2021                 NaN         20.00               NaN   
10/27/2021                 NaN         28.50             20.25   
10/28/2021                 NaN         19.50              7.75   
...                        ...           ...               ...   
04/02/2022                 NaN         31.50             25.75   
04/05/2022                 NaN         31.50               NaN   
04/06/2022                 NaN         35.75             43.50   
04/08/2022                 NaN         34.50              9.50   
04/10/2022                 NaN         40.25             38.00   

            De'Andre Hunter  Delon Wright  Gorgui Dieng  ...  Lou Williams  \
10/21/2021            20.75          9.50         26.00  ...           NaN   
10/23/2021            18.25         14.50         16.00  ...           NaN   
10/25/2021              NaN          9.00         24.00  ...         18.50   
10/27/2021            17.00         18.25          7.75  ...           NaN   
10/28/2021            16.50          1.50          7.75  ...          8.75   
...                     ...           ...           ...  ...           ...   
04/02/2022            31.00         23.00           NaN  ...         10.50   
04/05/2022            32.00         14.50           NaN  ...          4.50   
04/06/2022            21.00         19.50          0.00  ...           NaN   
04/08/2022             1.75         10.00           NaN  ...           NaN   
04/10/2022            25.50         11.00           NaN  ...           NaN   

            Malcolm Hill  Onyeka Okongwu  Sharife Cooper  Skylar Mays  \
10/21/2021           NaN             NaN             1.5         4.75   
10/23/2021           NaN             NaN             NaN          NaN   
10/25/2021           NaN             NaN             1.0         0.00   
10/27/2021           NaN             NaN             NaN          NaN   
10/28/2021           NaN             NaN             NaN          NaN   
...                  ...             ...             ...          ...   
04/02/2022           NaN           21.50             NaN          NaN   
04/05/2022           NaN            6.50             NaN          NaN   
04/06/2022           NaN           21.50             0.0         0.00   
04/08/2022           NaN           18.75             NaN          NaN   
04/10/2022           NaN           22.25             0.0         0.00   

            Solomon Hill  Timothe Luwawu-Cabarrot  Trae Young  Wes Iwundu  \
10/21/2021          8.00                     2.75       41.00         NaN   
10/23/2021         12.25                      NaN       41.25         NaN   
10/25/2021          5.00                     1.25       52.50         NaN   
10/27/2021           NaN                      NaN       47.25         NaN   
10/28/2021           NaN                      NaN       43.25         NaN   
...                  ...                      ...     

In [26]:
add = {}

values = {}

diff = {}

columns = tester.columns.tolist()[:-1]

#iterate through index
for column in columns:
    
    if column not in add:
        add[column] = []
        
        values[column] = []
        
        diff[column] = []
    
    print(column)
    
        # sequence
    df = tester[[column]]
    
    df["Min"] = tester_min[column].tolist()
    
    name = df.columns[0]
    
    rent_rate = array(df[name])
    
    # number of steps
    rent_rate = array(tester[column].dropna())
    predict = rent_rate
    eff = array(df["Min"].dropna())
    
    
    n_steps = 3
    if len(rent_rate) < 5:
        continue   
    
    
    # convert to [rows, columns] structure
    rent_rate = rent_rate.reshape((len(rent_rate), 1))
    eff = eff.reshape((len(eff), 1))
    predict = predict.reshape((len(predict), 1))
    
    # horizontally stack columns
    dataset = hstack((rent_rate, eff, predict))    
        
    X, y = split_sequence(dataset, n_steps)
    
    X = X.astype(float)
    # summarize the data
    for i in range(len(X)):
        print(X[i], y[i])
        
    # reshape from [samples, timesteps] into [samples, timesteps, features]
    n_features = X.shape[2]
    
    for num in range(len(rent_rate) - 4):
        
        value = rent_rate[3 + num][0]
        
        values[column].append(rent_rate[3 + num][0])
    
        rent = []
        pred = []
        for i in rent_rate[0 + num: 3 + num]:
            rent.append(i[0])
            pred.append(i[0])
        eff_pred = []
        for i in eff[0 + num: 3 + num]:
            eff_pred.append(i[0])

        # demonstrate prediction
        x_input = array([[rent[0], eff_pred[0]], [rent[1], eff_pred[1]], [rent[2], eff_pred[2]]])
        x_input = x_input.reshape((1, n_steps, n_features))
        yhat = model.predict(x_input, verbose=0)
        add[column].append(yhat.tolist()[0][0])
        
        pred = yhat.tolist()[0][0]
        
        perc = (pred - value)
        
        diff[column].append(perc)
        
    
    
        
    
    
    
    
    

Bogdan Bogdanovic
[[22.25       26.43333333]
 [11.         27.45      ]
 [20.25       25.41666667]] 20.25
[[11.         27.45      ]
 [20.25       25.41666667]
 [23.25       31.51666667]] 23.25
[[20.25       25.41666667]
 [23.25       31.51666667]
 [30.         33.55      ]] 30.0
[[23.25       31.51666667]
 [30.         33.55      ]
 [22.5        29.48333333]] 22.5
[[30.         33.55      ]
 [22.5        29.48333333]
 [34.5        34.56666667]] 34.5
[[22.5        29.48333333]
 [34.5        34.56666667]
 [19.5        29.48333333]] 19.5
[[34.5        34.56666667]
 [19.5        29.48333333]
 [17.75       29.48333333]] 17.75
[[19.5        29.48333333]
 [17.75       29.48333333]
 [27.75       29.48333333]] 27.75
[[17.75       29.48333333]
 [27.75       29.48333333]
 [23.75       31.51666667]] 23.75
[[27.75       29.48333333]
 [23.75       31.51666667]
 [18.5        29.48333333]] 18.5
[[23.75       31.51666667]
 [18.5        29.48333333]
 [14.5        29.48333333]] 14.5
[[18.5        29.483

/var/folders/g3/164q6cz52jv0sjllnsg7jdsm0000gn/T/ipykernel_5048/2686771382.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["Min"] = tester_min[column].tolist()
2022-11-09 07:57:15.746440: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:113] Plugin optimizer for device_type GPU is enabled.


Cam Reddish
[[27.25 21.35]
 [28.   27.45]
 [30.   27.45]] 30.0
[[28.         27.45      ]
 [30.         27.45      ]
 [10.75       23.38333333]] 10.75
[[30.         27.45      ]
 [10.75       23.38333333]
 [26.25       26.43333333]] 26.25
[[10.75       23.38333333]
 [26.25       26.43333333]
 [22.5        19.31666667]] 22.5
[[26.25       26.43333333]
 [22.5        19.31666667]
 [27.5        27.45      ]] 27.5
[[22.5        19.31666667]
 [27.5        27.45      ]
 [ 5.75       18.3       ]] 5.75
[[27.5        27.45      ]
 [ 5.75       18.3       ]
 [11.5        13.21666667]] 11.5
[[ 5.75       18.3       ]
 [11.5        13.21666667]
 [15.75       26.43333333]] 15.75
[[11.5        13.21666667]
 [15.75       26.43333333]
 [ 5.         13.21666667]] 5.0
[[15.75       26.43333333]
 [ 5.         13.21666667]
 [24.25       30.5       ]] 24.25
[[ 5.         13.21666667]
 [24.25       30.5       ]
 [14.5        18.3       ]] 14.5
[[24.25       30.5       ]
 [14.5        18.3       ]
 [13.25   

/var/folders/g3/164q6cz52jv0sjllnsg7jdsm0000gn/T/ipykernel_5048/2686771382.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["Min"] = tester_min[column].tolist()


Cameron Oliver
Cat Barber
Chaundee Brown Jr.
Clint Capela
[[31.75       20.33333333]
 [32.5        27.45      ]
 [20.         25.41666667]] 20.0
[[32.5        27.45      ]
 [20.         25.41666667]
 [28.5        29.48333333]] 28.5
[[20.         25.41666667]
 [28.5        29.48333333]
 [19.5        23.38333333]] 19.5
[[28.5        29.48333333]
 [19.5        23.38333333]
 [28.         27.45      ]] 28.0
[[19.5        23.38333333]
 [28.         27.45      ]
 [38.5        33.55      ]] 38.5
[[28.         27.45      ]
 [38.5        33.55      ]
 [36.5        32.53333333]] 36.5
[[38.5        33.55      ]
 [36.5        32.53333333]
 [30.5        35.58333333]] 30.5
[[36.5        32.53333333]
 [30.5        35.58333333]
 [26.75       28.46666667]] 26.75
[[30.5        35.58333333]
 [26.75       28.46666667]
 [14.         23.38333333]] 14.0
[[26.75       28.46666667]
 [14.         23.38333333]
 [39.         34.56666667]] 39.0
[[14.         23.38333333]
 [39.         34.56666667]
 [32.25       32.

...

/var/folders/g3/164q6cz52jv0sjllnsg7jdsm0000gn/T/ipykernel_5048/2686771382.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["Min"] = tester_min[column].tolist()


Trae Young
[[41.         32.53333333]
 [41.25       35.58333333]
 [52.5        32.53333333]] 52.5
[[41.25       35.58333333]
 [52.5        32.53333333]
 [47.25       36.6       ]] 47.25
[[52.5        32.53333333]
 [47.25       36.6       ]
 [43.25       34.56666667]] 43.25
[[47.25       36.6       ]
 [43.25       34.56666667]
 [29.5        31.51666667]] 29.5
[[43.25       34.56666667]
 [29.5        31.51666667]
 [39.5        36.6       ]] 39.5
[[29.5        31.51666667]
 [39.5        36.6       ]
 [47.25       36.6       ]] 47.25
[[39.5        36.6       ]
 [47.25       36.6       ]
 [39.5        34.56666667]] 39.5
[[47.25       36.6       ]
 [39.5        34.56666667]
 [52.         39.65      ]] 52.0
[[39.5        34.56666667]
 [52.         39.65      ]
 [47.25       32.53333333]] 47.25
[[52.         39.65      ]
 [47.25       32.53333333]
 [37.5        35.58333333]] 37.5
[[47.25       32.53333333]
 [37.5        35.58333333]
 [50.75       32.53333333]] 50.75
[[37.5        35.58333333]


/var/folders/g3/164q6cz52jv0sjllnsg7jdsm0000gn/T/ipykernel_5048/2686771382.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["Min"] = tester_min[column].tolist()


Wes Iwundu


/var/folders/g3/164q6cz52jv0sjllnsg7jdsm0000gn/T/ipykernel_5048/2686771382.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["Min"] = tester_min[column].tolist()


In [27]:
add = {}

values = {}

diff = {}

#iterate through index
for column in columns:
    
    if column not in add:
        add[column] = []
        
        values[column] = []
        
        diff[column] = []
    
    print(column)
    
        # sequence
    df = tester[[column]]
    
    df["Min"] = tester_min[column].tolist()
    
    name = df.columns[0]
    
    rent_rate = array(df[name])
    
    # number of steps
    rent_rate = array(tester[column].dropna())
    predict = rent_rate
    eff = array(df["Min"].dropna())
    
    
    n_steps = 3
    if len(rent_rate) < 5:
        continue   
    
    
    # convert to [rows, columns] structure
    rent_rate = rent_rate.reshape((len(rent_rate), 1))
    eff = eff.reshape((len(eff), 1))
    predict = predict.reshape((len(predict), 1))
    
    # horizontally stack columns
    dataset = hstack((rent_rate, eff, predict))    
        
    X, y = split_sequence(dataset, n_steps)
    
    X = X.astype(float)

    # reshape from [samples, timesteps] into [samples, timesteps, features]
    n_features = X.shape[2]
    
    for num in range(len(rent_rate) - 4):
        
        value = rent_rate[3 + num][0]
        
        
        values[column].append(rent_rate[3 + num][0])
    
        rent = []
        pred = []
        for i in rent_rate[0 + num: 3 + num]:
            rent.append(i[0])
            pred.append(i[0])
        eff_pred = []
        for i in eff[0 + num: 3 + num]:
            eff_pred.append(i[0])
            
        print(rent)
        print(value)

        # demonstrate prediction
        x_input = array([[rent[0], eff_pred[0]], [rent[1], eff_pred[1]], [rent[2], eff_pred[2]]])
        x_input = x_input.reshape((1, n_steps, n_features))
        yhat = model.predict(x_input, verbose=0)
        add[column].append(yhat.tolist()[0][0])
        
        pred = yhat.tolist()[0][0]
        
        perc = (pred - value)
        
        diff[column].append(perc)
        

Bogdan Bogdanovic
[22.25, 11.0, 20.25]
23.25
[11.0, 20.25, 23.25]
30.0
[20.25, 23.25, 30.0]
22.5
[23.25, 30.0, 22.5]
34.5
[30.0, 22.5, 34.5]
19.5
[22.5, 34.5, 19.5]
17.75


/var/folders/g3/164q6cz52jv0sjllnsg7jdsm0000gn/T/ipykernel_5048/697180837.py:22: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["Min"] = tester_min[column].tolist()


[34.5, 19.5, 17.75]
27.75
[19.5, 17.75, 27.75]
23.75
[17.75, 27.75, 23.75]
18.5
[27.75, 23.75, 18.5]
14.5
[23.75, 18.5, 14.5]
30.75
[18.5, 14.5, 30.75]
24.25
[14.5, 30.75, 24.25]
11.75
[30.75, 24.25, 11.75]
22.75
[24.25, 11.75, 22.75]
36.25
[11.75, 22.75, 36.25]
22.75
[22.75, 36.25, 22.75]
6.75
[36.25, 22.75, 6.75]
16.0
[22.75, 6.75, 16.0]
23.75
[6.75, 16.0, 23.75]
22.25
[16.0, 23.75, 22.25]
33.5
[23.75, 22.25, 33.5]
26.0
[22.25, 33.5, 26.0]
36.0
[33.5, 26.0, 36.0]
29.25
[26.0, 36.0, 29.25]
18.25
[36.0, 29.25, 18.25]
35.25
[29.25, 18.25, 35.25]
32.25
[18.25, 35.25, 32.25]
23.25
[35.25, 32.25, 23.25]
32.25
[32.25, 23.25, 32.25]
24.0
[23.25, 32.25, 24.0]
41.0
[32.25, 24.0, 41.0]
19.0
[24.0, 41.0, 19.0]
20.0
[41.0, 19.0, 20.0]
41.25
[19.0, 20.0, 41.25]
39.5
[20.0, 41.25, 39.5]
31.25
[41.25, 39.5, 31.25]
38.75
[39.5, 31.25, 38.75]
43.25
[31.25, 38.75, 43.25]
28.0
[38.75, 43.25, 28.0]
37.0
[43.25, 28.0, 37.0]
34.0
[28.0, 37.0, 34.0]
32.5
[37.0, 34.0, 32.5]
41.75
[34.0, 32.5, 41.75]
26.0
[32

/var/folders/g3/164q6cz52jv0sjllnsg7jdsm0000gn/T/ipykernel_5048/697180837.py:22: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["Min"] = tester_min[column].tolist()


[28.0, 30.0, 10.75]
26.25
[30.0, 10.75, 26.25]
22.5
[10.75, 26.25, 22.5]
27.5
[26.25, 22.5, 27.5]
5.75
[22.5, 27.5, 5.75]
11.5
[27.5, 5.75, 11.5]
15.75
[5.75, 11.5, 15.75]
5.0
[11.5, 15.75, 5.0]
24.25
[15.75, 5.0, 24.25]
14.5
[5.0, 24.25, 14.5]
13.25
[24.25, 14.5, 13.25]
17.75
[14.5, 13.25, 17.75]
31.0
[13.25, 17.75, 31.0]
25.0
[17.75, 31.0, 25.0]
16.75
[31.0, 25.0, 16.75]
18.25
[25.0, 16.75, 18.25]
26.25
[16.75, 18.25, 26.25]
3.0
[18.25, 26.25, 3.0]
6.5
[26.25, 3.0, 6.5]
21.5
[3.0, 6.5, 21.5]
21.75
[6.5, 21.5, 21.75]
7.5
[21.5, 21.75, 7.5]
51.5
[21.75, 7.5, 51.5]
24.75
[7.5, 51.5, 24.75]
25.5
[51.5, 24.75, 25.5]
44.0
[24.75, 25.5, 44.0]
22.75
[25.5, 44.0, 22.75]
8.0
[44.0, 22.75, 8.0]
29.5
[22.75, 8.0, 29.5]
3.5
Cameron Oliver
Cat Barber
Chaundee Brown Jr.
Clint Capela
[31.75, 32.5, 20.0]
28.5


...

/var/folders/g3/164q6cz52jv0sjllnsg7jdsm0000gn/T/ipykernel_5048/697180837.py:22: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["Min"] = tester_min[column].tolist()


[1.25, 3.25, 3.5]
10.5
[3.25, 3.5, 10.5]
1.25
[3.5, 10.5, 1.25]
2.0
[10.5, 1.25, 2.0]
3.5
[1.25, 2.0, 3.5]
0.0
[2.0, 3.5, 0.0]
0.0
[3.5, 0.0, 0.0]
0.0
[0.0, 0.0, 0.0]
4.0
[0.0, 0.0, 4.0]
8.0
[0.0, 4.0, 8.0]
5.5
[4.0, 8.0, 5.5]
16.25
[8.0, 5.5, 16.25]
3.25
[5.5, 16.25, 3.25]
25.0
[16.25, 3.25, 25.0]
34.0
[3.25, 25.0, 34.0]
8.5
[25.0, 34.0, 8.5]
15.25
[34.0, 8.5, 15.25]
13.0
[8.5, 15.25, 13.0]
12.5
[15.25, 13.0, 12.5]
14.25
[13.0, 12.5, 14.25]
24.5
[12.5, 14.25, 24.5]
8.25
[14.25, 24.5, 8.25]
22.0
[24.5, 8.25, 22.0]
10.5
[8.25, 22.0, 10.5]
7.75
[22.0, 10.5, 7.75]
5.5
[10.5, 7.75, 5.5]
-0.5
[7.75, 5.5, -0.5]
3.5
[5.5, -0.5, 3.5]
0.0
[-0.5, 3.5, 0.0]
3.5
[3.5, 0.0, 3.5]
9.0
[0.0, 3.5, 9.0]
8.0
[3.5, 9.0, 8.0]
3.25
[9.0, 8.0, 3.25]
0.0
[8.0, 3.25, 0.0]
0.0
[3.25, 0.0, 0.0]
0.0
[0.0, 0.0, 0.0]
8.0
[0.0, 0.0, 8.0]
6.25
[0.0, 8.0, 6.25]
14.75
[8.0, 6.25, 14.75]
4.25
[6.25, 14.75, 4.25]
6.0
[14.75, 4.25, 6.0]
12.5
[4.25, 6.0, 12.5]
24.0
[6.0, 12.5, 24.0]
21.25
[12.5, 24.0, 21.25]
22.0
[24.0, 21

/var/folders/g3/164q6cz52jv0sjllnsg7jdsm0000gn/T/ipykernel_5048/697180837.py:22: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["Min"] = tester_min[column].tolist()


[41.25, 52.5, 47.25]
43.25
[52.5, 47.25, 43.25]
29.5
[47.25, 43.25, 29.5]
39.5
[43.25, 29.5, 39.5]
47.25
[29.5, 39.5, 47.25]
39.5
[39.5, 47.25, 39.5]
52.0
[47.25, 39.5, 52.0]
47.25
[39.5, 52.0, 47.25]
37.5
[52.0, 47.25, 37.5]
50.75
[47.25, 37.5, 50.75]
70.5
[37.5, 50.75, 70.5]
38.0
[50.75, 70.5, 38.0]
33.5
[70.5, 38.0, 33.5]
38.5
[38.0, 33.5, 38.5]
47.5
[33.5, 38.5, 47.5]
60.25
[38.5, 47.5, 60.25]
46.75
[47.5, 60.25, 46.75]
49.5
[60.25, 46.75, 49.5]
61.5
[46.75, 49.5, 61.5]
46.0
[49.5, 61.5, 46.0]
53.5
[61.5, 46.0, 53.5]
57.75
[46.0, 53.5, 57.75]
56.25
[53.5, 57.75, 56.25]
60.5
[57.75, 56.25, 60.5]
43.0
[56.25, 60.5, 43.0]
55.25
[60.5, 43.0, 55.25]
43.25
[43.0, 55.25, 43.25]
43.75
[55.25, 43.25, 43.75]
60.5
[43.25, 43.75, 60.5]
83.5
[43.75, 60.5, 83.5]
53.25
[60.5, 83.5, 53.25]
38.25
[83.5, 53.25, 38.25]
26.75
[53.25, 38.25, 26.75]
40.75
[38.25, 26.75, 40.75]
46.25
[26.75, 40.75, 46.25]
53.0
[40.75, 46.25, 53.0]
66.75
[46.25, 53.0, 66.75]
42.25
[53.0, 66.75, 42.25]
46.0
[66.75, 42.25, 

/var/folders/g3/164q6cz52jv0sjllnsg7jdsm0000gn/T/ipykernel_5048/697180837.py:22: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["Min"] = tester_min[column].tolist()


In [33]:
pred

[43661.4765625]

In [28]:
diff

{'Bogdan Bogdanovic': [array([25464.71679688]),
  array([27278.99023438]),
  array([31408.79492188]),
  array([30501.56054688]),
  array([35537.59765625]),
  array([29662.69335938]),
  array([29848.65429688]),
  array([29869.70898438]),
  array([29571.515625]),
  array([28698.26953125]),
  array([26939.52148438]),
  array([30290.28320312]),
  array([29469.625]),
  array([25510.10742188]),
  array([27929.73828125]),
  array([28843.2265625]),
  array([28073.36914062]),
  array([19559.625]),
  array([19857.37695312]),
  array([20551.09179688]),
  array([27673.88476562]),
  array([36526.22265625]),
  array([33054.484375]),
  array([36581.2265625]),
  array([31949.63476562]),
  array([28217.40625]),
  array([29386.66601562]),
  array([27540.2265625]),
  array([28409.23632812]),
  array([31893.43554688]),
  array([31173.953125]),
  array([36851.93359375]),
  array([29914.54492188]),
  array([27154.18945312]),
  array([29212.890625]),
  array([33373.63671875]),
  array([34780.3125]),
  array(

In [29]:
values

{'Bogdan Bogdanovic': [23.25,
  30.0,
  22.5,
  34.5,
  19.5,
  17.75,
  27.75,
  23.75,
  18.5,
  14.5,
  30.75,
  24.25,
  11.75,
  22.75,
  36.25,
  22.75,
  6.75,
  16.0,
  23.75,
  22.25,
  33.5,
  26.0,
  36.0,
  29.25,
  18.25,
  35.25,
  32.25,
  23.25,
  32.25,
  24.0,
  41.0,
  19.0,
  20.0,
  41.25,
  39.5,
  31.25,
  38.75,
  43.25,
  28.0,
  37.0,
  34.0,
  32.5,
  41.75,
  26.0,
  25.75,
  31.0,
  26.25,
  21.0,
  45.0,
  30.0,
  49.0,
  23.0,
  37.25,
  32.0,
  16.5,
  15.75,
  38.75,
  29.5,
  42.25],
 'Cam Reddish': [10.75,
  26.25,
  22.5,
  27.5,
  5.75,
  11.5,
  15.75,
  5.0,
  24.25,
  14.5,
  13.25,
  17.75,
  31.0,
  25.0,
  16.75,
  18.25,
  26.25,
  3.0,
  6.5,
  21.5,
  21.75,
  7.5,
  51.5,
  24.75,
  25.5,
  44.0,
  22.75,
  8.0,
  29.5,
  3.5],
 'Cameron Oliver': [],
 'Cat Barber': [],
 'Chaundee Brown Jr.': [],
 'Clint Capela': [28.5,
  19.5,
  28.0,
  38.5,
  36.5,
  30.5,
  26.75,
  14.0,
  39.0,
  32.25,
  33.75,
  54.0,
  32.0,
  43.75,
  27.0,
  44.7

In [30]:
add

{'Bogdan Bogdanovic': [[25487.966796875],
  [27308.990234375],
  [31431.294921875],
  [30536.060546875],
  [35557.09765625],
  [29680.443359375],
  [29876.404296875],
  [29893.458984375],
  [29590.015625],
  [28712.76953125],
  [26970.271484375],
  [30314.533203125],
  [29481.375],
  [25532.857421875],
  [27965.98828125],
  [28865.9765625],
  [28080.119140625],
  [19575.625],
  [19881.126953125],
  [20573.341796875],
  [27707.384765625],
  [36552.22265625],
  [33090.484375],
  [36610.4765625],
  [31967.884765625],
  [28252.65625],
  [29418.916015625],
  [27563.4765625],
  [28441.486328125],
  [31917.435546875],
  [31214.953125],
  [36870.93359375],
  [29934.544921875],
  [27195.439453125],
  [29252.390625],
  [33404.88671875],
  [34819.0625],
  [34186.171875],
  [36439.03515625],
  [33309.453125],
  [39037.5390625],
  [34083.8359375],
  [36492.96484375],
  [39285.640625],
  [34940.890625],
  [33646.5703125],
  [32169.75390625],
  [28511.013671875],
  [29529.36328125],
  [31953.25390625

# Multiple Parallel Inputs

In [97]:
#obtain list of dates
directory = f"Historical/{teams[29]}"
list_dates = []
names = []
for filename in os.listdir(directory):
    names.append(filename)
    if filename.endswith(".csv"):
        list_dates.append(filename)

# create dictionary 
final_data = {}

# for minutes

minutes = {}

opponents = {}
# reads in each csv
for i in list_dates:
    data = pd.read_csv(f"{directory}/{i}", index_col=0)
    #gathers data and adds to dict
    date = data["Date"].tolist()[0]

    min_data = data.copy()



    minute = data["MIN"].tolist()

    minute_array = []

    for i in minute:
        time = i.split(":")

        minute_array.append(int(time[0]) + (int(time[0]) / 60))

    # (error for now) opponents[date] = data["Opponent"][0]

    data["MIN"] = minute_array

    data[date] = data["Score"]
    min_data[date] = data["MIN"]

    final_data[date] = data[date]
    minutes[date] = min_data[date]

# convert dict to dataframe
data_df = pd.DataFrame(final_data)

# convert dict to dataframe
min_df = pd.DataFrame(minutes)

opp = pd.DataFrame.transpose(pd.DataFrame.from_dict(opponents, orient="index"))
data_df = data_df.append(opp)

tester = pd.DataFrame.transpose(data_df)

tester["Datetime"] = pd.to_datetime(data_df.columns.tolist()).tolist()

tester = tester.sort_values(by="Datetime")

columns = tester.columns.tolist()[:-1]

tester_min = pd.DataFrame.transpose(min_df)

tester_min["Datetime"] = pd.to_datetime(min_df.columns.tolist()).tolist()

tester_min = tester_min.sort_values(by="Datetime")

columns = tester_min.columns.tolist()[:-1]

add = {}

/var/folders/g3/164q6cz52jv0sjllnsg7jdsm0000gn/T/ipykernel_5048/2754215829.py:54: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data_df = data_df.append(opp)


In [93]:
constant = 0

for t in range(len(teams) - 1):


    #obtain list of dates
    directory = f"Historical/{teams[t]}"
    list_dates = []
    names = []
    for filename in os.listdir(directory):
        names.append(filename)
        if filename.endswith(".csv"):
            list_dates.append(filename)

    # create dictionary 
    final_data = {}

    # for minutes

    minutes = {}

    opponents = {}
    # reads in each csv
    for i in list_dates:
        data = pd.read_csv(f"{directory}/{i}", index_col=0)
        #gathers data and adds to dict
        date = data["Date"].tolist()[0]

        min_data = data.copy()



        minute = data["MIN"].tolist()

        minute_array = []

        for i in minute:
            time = i.split(":")

            minute_array.append(int(time[0]) + (int(time[0]) / 60))

        # (error for now) opponents[date] = data["Opponent"][0]

        data["MIN"] = minute_array

        data[date] = data["Score"]
        min_data[date] = data["MIN"]

        final_data[date] = data[date]
        minutes[date] = min_data[date]

    # convert dict to dataframe
    data_df = pd.DataFrame(final_data)
    
    # convert dict to dataframe
    min_df = pd.DataFrame(minutes)
    
    opp = pd.DataFrame.transpose(pd.DataFrame.from_dict(opponents, orient="index"))
    data_df = data_df.append(opp)

    tester = pd.DataFrame.transpose(data_df)

    tester["Datetime"] = pd.to_datetime(data_df.columns.tolist()).tolist()

    tester = tester.sort_values(by="Datetime")

    columns = tester.columns.tolist()[:-1]

    tester_min = pd.DataFrame.transpose(min_df)

    tester_min["Datetime"] = pd.to_datetime(min_df.columns.tolist()).tolist()

    tester_min = tester_min.sort_values(by="Datetime")

    columns = tester_min.columns.tolist()[:-1]

    add = {}

    #iterate through index
    for column in columns:
        print(column)

    # univariate data prep LSTM

        # split sequence
        def split_sequence(sequences, n_steps):
            X, y = list(), list()
            for i in range(len(sequences)):
                # find end of pattern 
                end_ix = i + n_steps
                #check if beyond sequence to break
                if end_ix > len(sequences) - 1:
                    break
                #gather input and output parts of the pattern
                seq_x, seq_y = sequences[i:end_ix, :], sequences[end_ix, :]
                X.append(seq_x)
                y.append(seq_y)
            return array(X), array(y)
        # sequence
        df = tester[[column]]

        df["Min"] = tester_min[column].tolist()

        name = df.columns[0]

        rent_rate = array(df[name])

        eff = array(df["Min"])

        predict = rent_rate

        # number of steps
        rent_rate = array(tester[column].dropna())
        predict = rent_rate
        eff = array(df["Min"].dropna())



        # convert to [rows, columns] structure
        rent_rate = rent_rate.reshape((len(rent_rate), 1))
        eff = eff.reshape((len(eff), 1))

        n_steps = 3

        # number of steps
        n_steps_in, n_steps_out = 3, 2
        if len(rent_rate) < 5:
            continue   

        # horizontally stack columns
        dataset = hstack((rent_rate, eff))    

        X, y = split_sequence(dataset, n_steps_in)

        X = X.astype(float)
        # summarize the data
        for i in range(len(X)):
            print(X[i], y[i])

        # reshape from [samples, timesteps] into [samples, timesteps, features]
        n_features = X.shape[2]
        
        opt = 'adam'

        if t == 0 and constant == 0:

                print("True")
                model = Sequential()
                model.add(LSTM(50, activation='relu', input_shape=(n_steps, n_features)))
                model.add(Dense(n_features))
                model.compile(optimizer='adam', loss='mse')

                # X_old = X.copy()

                # y_old = y.copy()

                # fit model
                model.fit(X, y, epochs=200, batch_size=32, verbose=0)

        else:

            # create a composite dataset of old and new data
            # X_both, y_both = vstack((X_old, X)), hstack((y_old, y))
            # fit the model on new data
            model.fit(X, y, epochs=100, batch_size=32, verbose=0)
            
            # X_old = X_both
            
            # y_old = y_both
            
        constant += 1




Anthony Edwards
[[44.         31.51666667]
 [42.75       36.6       ]
 [46.25       40.66666667]] [40.25 33.55]
[[42.75       36.6       ]
 [46.25       40.66666667]
 [40.25       33.55      ]] [27.75       34.56666667]
[[46.25       40.66666667]
 [40.25       33.55      ]
 [27.75       34.56666667]] [40.  36.6]
[[40.25       33.55      ]
 [27.75       34.56666667]
 [40.         36.6       ]] [47.25       38.63333333]
[[27.75       34.56666667]
 [40.         36.6       ]
 [47.25       38.63333333]] [33.25       31.51666667]
[[40.         36.6       ]
 [47.25       38.63333333]
 [33.25       31.51666667]] [43.75 42.7 ]
[[47.25       38.63333333]
 [33.25       31.51666667]
 [43.75       42.7       ]] [67.5        41.68333333]
[[33.25       31.51666667]
 [43.75       42.7       ]
 [67.5        41.68333333]] [14.25       32.53333333]
[[43.75       42.7       ]
 [67.5        41.68333333]
 [14.25       32.53333333]] [38.25       34.56666667]
[[67.5        41.68333333]
 [14.25       32.533333

/var/folders/g3/164q6cz52jv0sjllnsg7jdsm0000gn/T/ipykernel_5048/1743353131.py:59: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  data_df = data_df.append(opp)
/var/folders/g3/164q6cz52jv0sjllnsg7jdsm0000gn/T/ipykernel_5048/1743353131.py:102: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["Min"] = tester_min[column].tolist()
2022-11-09 18:01:30.057896: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:113] Plugin optimizer for device_type GPU is enabled.


Chris Silva
D'Angelo Russell
[[40.75       24.4       ]
 [14.75       29.48333333]
 [28.         29.48333333]] [44.25 36.6 ]
[[14.75       29.48333333]
 [28.         29.48333333]
 [44.25       36.6       ]] [29.75       31.51666667]
[[28.         29.48333333]
 [44.25       36.6       ]
 [29.75       31.51666667]] [15.75       16.26666667]
[[44.25       36.6       ]
 [29.75       31.51666667]
 [15.75       16.26666667]] [52.75       40.66666667]
[[29.75       31.51666667]
 [15.75       16.26666667]
 [52.75       40.66666667]] [31.75       34.56666667]
[[15.75       16.26666667]
 [52.75       40.66666667]
 [31.75       34.56666667]] [41.25 33.55]
[[52.75       40.66666667]
 [31.75       34.56666667]
 [41.25       33.55      ]] [35.  30.5]
[[31.75       34.56666667]
 [41.25       33.55      ]
 [35.         30.5       ]] [35.         34.56666667]
[[41.25       33.55      ]
 [35.         30.5       ]
 [35.         34.56666667]] [38.         34.56666667]
[[35.         30.5       ]
 [35.     

/var/folders/g3/164q6cz52jv0sjllnsg7jdsm0000gn/T/ipykernel_5048/1743353131.py:102: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["Min"] = tester_min[column].tolist()
/var/folders/g3/164q6cz52jv0sjllnsg7jdsm0000gn/T/ipykernel_5048/1743353131.py:102: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["Min"] = tester_min[column].tolist()


Greg Monroe
Jaden McDaniels
[[22.         25.41666667]
 [15.         27.45      ]
 [12.         32.53333333]] [21.25       31.51666667]
[[15.         27.45      ]
 [12.         32.53333333]
 [21.25       31.51666667]] [ 8.  24.4]
[[12.         32.53333333]
 [21.25       31.51666667]
 [ 8.         24.4       ]] [12.5        17.28333333]
[[21.25       31.51666667]
 [ 8.         24.4       ]
 [12.5        17.28333333]] [ 9.75       28.46666667]
[[ 8.         24.4       ]
 [12.5        17.28333333]
 [ 9.75       28.46666667]] [11.  12.2]
[[12.5        17.28333333]
 [ 9.75       28.46666667]
 [11.         12.2       ]] [25.25       31.51666667]
[[ 9.75       28.46666667]
 [11.         12.2       ]
 [25.25       31.51666667]] [ 5.25       14.23333333]
[[11.         12.2       ]
 [25.25       31.51666667]
 [ 5.25       14.23333333]] [18.   21.35]
[[25.25       31.51666667]
 [ 5.25       14.23333333]
 [18.         21.35      ]] [29.5        32.53333333]
[[ 5.25       14.23333333]
 [18.        

...

/var/folders/g3/164q6cz52jv0sjllnsg7jdsm0000gn/T/ipykernel_5048/1743353131.py:102: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["Min"] = tester_min[column].tolist()


Wayne Ellington
[[ 7.5         8.13333333]
 [13.5        24.4       ]
 [11.5        23.38333333]] [17.   21.35]
[[13.5        24.4       ]
 [11.5        23.38333333]
 [17.         21.35      ]] [ 6.5  27.45]
[[11.5        23.38333333]
 [17.         21.35      ]
 [ 6.5        27.45      ]] [24.5        29.48333333]
[[17.         21.35      ]
 [ 6.5        27.45      ]
 [24.5        29.48333333]] [ 9.25       20.33333333]
[[ 6.5        27.45      ]
 [24.5        29.48333333]
 [ 9.25       20.33333333]] [ 7.25       19.31666667]
[[24.5        29.48333333]
 [ 9.25       20.33333333]
 [ 7.25       19.31666667]] [ 1.25       11.18333333]
[[ 9.25       20.33333333]
 [ 7.25       19.31666667]
 [ 1.25       11.18333333]] [ 5.75       11.18333333]
[[ 7.25       19.31666667]
 [ 1.25       11.18333333]
 [ 5.75       11.18333333]] [ 4.75       17.28333333]
[[ 1.25       11.18333333]
 [ 5.75       11.18333333]
 [ 4.75       17.28333333]] [24.         29.48333333]
[[ 5.75       11.18333333]
 [ 4.75  

/var/folders/g3/164q6cz52jv0sjllnsg7jdsm0000gn/T/ipykernel_5048/1743353131.py:102: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["Min"] = tester_min[column].tolist()


Wenyen Gabriel
[[ 7.25        3.05      ]
 [ 3.5         2.03333333]
 [10.         12.2       ]] [11.25 12.2 ]
[[ 3.5         2.03333333]
 [10.         12.2       ]
 [11.25       12.2       ]] [16.75 18.3 ]
[[10.   12.2 ]
 [11.25 12.2 ]
 [16.75 18.3 ]] [14.5        14.23333333]
[[11.25       12.2       ]
 [16.75       18.3       ]
 [14.5        14.23333333]] [26.75 24.4 ]
[[16.75       18.3       ]
 [14.5        14.23333333]
 [26.75       24.4       ]] [ 8.5        11.18333333]
[[14.5        14.23333333]
 [26.75       24.4       ]
 [ 8.5        11.18333333]] [20.5        31.51666667]
[[26.75       24.4       ]
 [ 8.5        11.18333333]
 [20.5        31.51666667]] [23.25       29.48333333]
[[ 8.5        11.18333333]
 [20.5        31.51666667]
 [23.25       29.48333333]] [ 7.5        17.28333333]
[[20.5        31.51666667]
 [23.25       29.48333333]
 [ 7.5        17.28333333]] [16.75 15.25]
[[23.25       29.48333333]
 [ 7.5        17.28333333]
 [16.75       15.25      ]] [12.75       10

/var/folders/g3/164q6cz52jv0sjllnsg7jdsm0000gn/T/ipykernel_5048/1743353131.py:102: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["Min"] = tester_min[column].tolist()


In [94]:
t

28

30

In [98]:
add = {}

values = {}

diff = {}

columns = tester.columns.tolist()[:-1]

#iterate through index
for column in columns:
    
    if column not in add:
        add[column] = []
        
        values[column] = []
        
        diff[column] = []
    
    print(column)
    
        # sequence
    df = tester[[column]]
    
    df["Min"] = tester_min[column].tolist()
    
    name = df.columns[0]
    
    rent_rate = array(df[name])
    
    # number of steps
    rent_rate = array(tester[column].dropna())
    predict = rent_rate
    eff = array(df["Min"].dropna())
    
    
    n_steps = 3
    if len(rent_rate) < 5:
        continue   
    
    
    # convert to [rows, columns] structure
    rent_rate = rent_rate.reshape((len(rent_rate), 1))
    eff = eff.reshape((len(eff), 1))
    predict = predict.reshape((len(predict), 1))
    
    # horizontally stack columns
    dataset = hstack((rent_rate, eff))    
        
    X, y = split_sequence(dataset, n_steps)
    
    X = X.astype(float)
    # summarize the data
    for i in range(len(X)):
        print(X[i], y[i])
        
    # reshape from [samples, timesteps] into [samples, timesteps, features]
    n_features = X.shape[2]
    
    for num in range(len(rent_rate) - 4):
        
        value = rent_rate[3 + num][0]
        
        values[column].append(rent_rate[3 + num][0])
    
        rent = []
        pred = []
        for i in rent_rate[0 + num: 3 + num]:
            rent.append(i[0])
            pred.append(i[0])
        eff_pred = []
        for i in eff[0 + num: 3 + num]:
            eff_pred.append(i[0])

        # demonstrate prediction
        x_input = array([[rent[0], eff_pred[0]], [rent[1], eff_pred[1]], [rent[2], eff_pred[2]]])
        x_input = x_input.reshape((1, n_steps, n_features))
        yhat = model.predict(x_input, verbose=0)
        add[column].append(yhat.tolist()[0][0])
        
        pred = yhat.tolist()[0][0]
        
        perc = (pred - value)
        
        diff[column].append(perc)
        
    
    
    

Bogdan Bogdanovic
[[22.25       26.43333333]
 [11.         27.45      ]
 [20.25       25.41666667]] [23.25       31.51666667]
[[11.         27.45      ]
 [20.25       25.41666667]
 [23.25       31.51666667]] [30.   33.55]
[[20.25       25.41666667]
 [23.25       31.51666667]
 [30.         33.55      ]] [22.5        29.48333333]
[[23.25       31.51666667]
 [30.         33.55      ]
 [22.5        29.48333333]] [34.5        34.56666667]
[[30.         33.55      ]
 [22.5        29.48333333]
 [34.5        34.56666667]] [19.5        29.48333333]
[[22.5        29.48333333]
 [34.5        34.56666667]
 [19.5        29.48333333]] [17.75       29.48333333]
[[34.5        34.56666667]
 [19.5        29.48333333]
 [17.75       29.48333333]] [27.75       29.48333333]
[[19.5        29.48333333]
 [17.75       29.48333333]
 [27.75       29.48333333]] [23.75       31.51666667]
[[17.75       29.48333333]
 [27.75       29.48333333]
 [23.75       31.51666667]] [18.5        29.48333333]
[[27.75       29.48333

/var/folders/g3/164q6cz52jv0sjllnsg7jdsm0000gn/T/ipykernel_5048/2642397829.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["Min"] = tester_min[column].tolist()
2022-11-09 20:10:50.722054: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:113] Plugin optimizer for device_type GPU is enabled.


Cam Reddish
[[27.25 21.35]
 [28.   27.45]
 [30.   27.45]] [10.75       23.38333333]
[[28.         27.45      ]
 [30.         27.45      ]
 [10.75       23.38333333]] [26.25       26.43333333]
[[30.         27.45      ]
 [10.75       23.38333333]
 [26.25       26.43333333]] [22.5        19.31666667]
[[10.75       23.38333333]
 [26.25       26.43333333]
 [22.5        19.31666667]] [27.5  27.45]
[[26.25       26.43333333]
 [22.5        19.31666667]
 [27.5        27.45      ]] [ 5.75 18.3 ]
[[22.5        19.31666667]
 [27.5        27.45      ]
 [ 5.75       18.3       ]] [11.5        13.21666667]
[[27.5        27.45      ]
 [ 5.75       18.3       ]
 [11.5        13.21666667]] [15.75       26.43333333]
[[ 5.75       18.3       ]
 [11.5        13.21666667]
 [15.75       26.43333333]] [ 5.         13.21666667]
[[11.5        13.21666667]
 [15.75       26.43333333]
 [ 5.         13.21666667]] [24.25 30.5 ]
[[15.75       26.43333333]
 [ 5.         13.21666667]
 [24.25       30.5       ]] [14.5 

/var/folders/g3/164q6cz52jv0sjllnsg7jdsm0000gn/T/ipykernel_5048/2642397829.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["Min"] = tester_min[column].tolist()


Cameron Oliver
Cat Barber
Chaundee Brown Jr.
Clint Capela
[[31.75       20.33333333]
 [32.5        27.45      ]
 [20.         25.41666667]] [28.5        29.48333333]
[[32.5        27.45      ]
 [20.         25.41666667]
 [28.5        29.48333333]] [19.5        23.38333333]
[[20.         25.41666667]
 [28.5        29.48333333]
 [19.5        23.38333333]] [28.   27.45]
[[28.5        29.48333333]
 [19.5        23.38333333]
 [28.         27.45      ]] [38.5  33.55]
[[19.5        23.38333333]
 [28.         27.45      ]
 [38.5        33.55      ]] [36.5        32.53333333]
[[28.         27.45      ]
 [38.5        33.55      ]
 [36.5        32.53333333]] [30.5        35.58333333]
[[38.5        33.55      ]
 [36.5        32.53333333]
 [30.5        35.58333333]] [26.75       28.46666667]
[[36.5        32.53333333]
 [30.5        35.58333333]
 [26.75       28.46666667]] [14.         23.38333333]
[[30.5        35.58333333]
 [26.75       28.46666667]
 [14.         23.38333333]] [39.         34.5666

...

/var/folders/g3/164q6cz52jv0sjllnsg7jdsm0000gn/T/ipykernel_5048/2642397829.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["Min"] = tester_min[column].tolist()


Trae Young
[[41.         32.53333333]
 [41.25       35.58333333]
 [52.5        32.53333333]] [47.25 36.6 ]
[[41.25       35.58333333]
 [52.5        32.53333333]
 [47.25       36.6       ]] [43.25       34.56666667]
[[52.5        32.53333333]
 [47.25       36.6       ]
 [43.25       34.56666667]] [29.5        31.51666667]
[[47.25       36.6       ]
 [43.25       34.56666667]
 [29.5        31.51666667]] [39.5 36.6]
[[43.25       34.56666667]
 [29.5        31.51666667]
 [39.5        36.6       ]] [47.25 36.6 ]
[[29.5        31.51666667]
 [39.5        36.6       ]
 [47.25       36.6       ]] [39.5        34.56666667]
[[39.5        36.6       ]
 [47.25       36.6       ]
 [39.5        34.56666667]] [52.   39.65]
[[47.25       36.6       ]
 [39.5        34.56666667]
 [52.         39.65      ]] [47.25       32.53333333]
[[39.5        34.56666667]
 [52.         39.65      ]
 [47.25       32.53333333]] [37.5        35.58333333]
[[52.         39.65      ]
 [47.25       32.53333333]
 [37.5       

/var/folders/g3/164q6cz52jv0sjllnsg7jdsm0000gn/T/ipykernel_5048/2642397829.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["Min"] = tester_min[column].tolist()


Wes Iwundu


/var/folders/g3/164q6cz52jv0sjllnsg7jdsm0000gn/T/ipykernel_5048/2642397829.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["Min"] = tester_min[column].tolist()


In [99]:
diff

{'Bogdan Bogdanovic': [-11.362542152404785,
  -14.419524192810059,
  -4.189109802246094,
  -17.713199615478516,
  2.638479232788086,
  -13.841747522354126,
  -4.831897735595703,
  -3.8230724334716797,
  3.5519580841064453,
  2.937847137451172,
  -13.621271133422852,
  -4.071279525756836,
  13.561256408691406,
  -15.360820770263672,
  -18.510038375854492,
  0.30263710021972656,
  4.4853363037109375,
  -0.8937349319458008,
  -8.510838508605957,
  -11.977801322937012,
  -17.52637004852295,
  -12.533514976501465,
  -12.215644836425781,
  0.392852783203125,
  10.072254180908203,
  -22.86880588531494,
  -7.863136291503906,
  -2.6721458435058594,
  -19.543859481811523,
  -3.1945133209228516,
  -24.292165756225586,
  -3.0715837478637695,
  -6.599921226501465,
  -30.724485397338867,
  -16.30261993408203,
  -9.82577133178711,
  -26.009526252746582,
  -16.039138793945312,
  9.344249725341797,
  -24.322481155395508,
  -5.030172348022461,
  -1.5425033569335938,
  -16.836938858032227,
  -17.65736865

In [100]:
add

{'Bogdan Bogdanovic': [11.887457847595215,
  15.580475807189941,
  18.310890197753906,
  16.786800384521484,
  22.138479232788086,
  3.908252477645874,
  22.918102264404297,
  19.92692756652832,
  22.051958084106445,
  17.437847137451172,
  17.12872886657715,
  20.178720474243164,
  25.311256408691406,
  7.389179229736328,
  17.739961624145508,
  23.052637100219727,
  11.235336303710938,
  15.1062650680542,
  15.239161491394043,
  10.272198677062988,
  15.97362995147705,
  13.466485023498535,
  23.78435516357422,
  29.642852783203125,
  28.322254180908203,
  12.381194114685059,
  24.386863708496094,
  20.57785415649414,
  12.706140518188477,
  20.80548667907715,
  16.707834243774414,
  15.92841625213623,
  13.400078773498535,
  10.525514602661133,
  23.19738006591797,
  21.42422866821289,
  12.740473747253418,
  27.210861206054688,
  37.3442497253418,
  12.677518844604492,
  28.96982765197754,
  30.957496643066406,
  24.913061141967773,
  8.342631340026855,
  12.186037063598633,
  27.1

In [101]:
values

{'Bogdan Bogdanovic': [23.25,
  30.0,
  22.5,
  34.5,
  19.5,
  17.75,
  27.75,
  23.75,
  18.5,
  14.5,
  30.75,
  24.25,
  11.75,
  22.75,
  36.25,
  22.75,
  6.75,
  16.0,
  23.75,
  22.25,
  33.5,
  26.0,
  36.0,
  29.25,
  18.25,
  35.25,
  32.25,
  23.25,
  32.25,
  24.0,
  41.0,
  19.0,
  20.0,
  41.25,
  39.5,
  31.25,
  38.75,
  43.25,
  28.0,
  37.0,
  34.0,
  32.5,
  41.75,
  26.0,
  25.75,
  31.0,
  26.25,
  21.0,
  45.0,
  30.0,
  49.0,
  23.0,
  37.25,
  32.0,
  16.5,
  15.75,
  38.75,
  29.5,
  42.25],
 'Cam Reddish': [10.75,
  26.25,
  22.5,
  27.5,
  5.75,
  11.5,
  15.75,
  5.0,
  24.25,
  14.5,
  13.25,
  17.75,
  31.0,
  25.0,
  16.75,
  18.25,
  26.25,
  3.0,
  6.5,
  21.5,
  21.75,
  7.5,
  51.5,
  24.75,
  25.5,
  44.0,
  22.75,
  8.0,
  29.5,
  3.5],
 'Cameron Oliver': [],
 'Cat Barber': [],
 'Chaundee Brown Jr.': [],
 'Clint Capela': [28.5,
  19.5,
  28.0,
  38.5,
  36.5,
  30.5,
  26.75,
  14.0,
  39.0,
  32.25,
  33.75,
  54.0,
  32.0,
  43.75,
  27.0,
  44.7

In [102]:
model.save("Multiple_Parallel.h5")

In [ ]:
    add = {}

    #iterate through index
    for column in columns:
        print(column)

    # univariate data prep LSTM

        # split sequence
        def split_sequence(sequences, n_steps):
            X, y = list(), list()
            for i in range(len(sequences)):
                # find end of pattern 
                end_ix = i + n_steps
                #check if beyond sequence to break
                if end_ix > len(sequences) - 1:
                    break
                #gather input and output parts of the pattern
                seq_x, seq_y = sequences[i:end_ix, :], sequences[end_ix, :]
                X.append(seq_x)
                y.append(seq_y)
            return array(X), array(y)
        # sequence
        df = tester[[column]]

        df["Min"] = tester_min[column].tolist()

        name = df.columns[0]

        rent_rate = array(df[name])

        eff = array(df["Min"])

        predict = rent_rate

        # number of steps
        rent_rate = array(tester[column].dropna())
        predict = rent_rate
        eff = array(df["Min"].dropna())



        # convert to [rows, columns] structure
        rent_rate = rent_rate.reshape((len(rent_rate), 1))
        eff = eff.reshape((len(eff), 1))

        n_steps = 3

        # number of steps
        n_steps_in, n_steps_out = 3, 2
        if len(rent_rate) < 5:
            continue   

        # horizontally stack columns
        dataset = hstack((rent_rate, eff))    

        X, y = split_sequence(dataset, n_steps_in)

        X = X.astype(float)
        # summarize the data
        for i in range(len(X)):
            print(X[i], y[i])

        # reshape from [samples, timesteps] into [samples, timesteps, features]
        n_features = X.shape[2]

        model = Sequential()
        model.add(LSTM(50, activation='relu', input_shape=(n_steps, n_features)))
        model.add(Dense(n_features))
        model.compile(optimizer='adam', loss='mse')

        # fit model
        model.fit(X, y, epochs=200, verbose=0)

## Normalize Data